![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 8. <i>Wykorzystanie tłumaczenia automatycznego we wspomaganiu tłumaczenia</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

W dzisiejszych czasach, niezwykle ważną techniką wspomagania tłumaczenia jest użycie tłumaczenia maszynowego. Tekst źródłowy do tłumaczenia jest najpierw tłumaczony całkowicie autommatycznie, a następnie tłumacz ludzki dokonuje korekty wyniku. Technologia tłumaczenia maszynowego jest już na tyle dojrzała, że oferuje bardzo wysoką jakość wyników. Coraz częstsze stają się scenariusze, w których ludzka korekta to niemal całkowicie machinalne (sic!) zatwierdzanie wyników tłumaczenia maszynowego. Na dzisiejszych zajęciach poznamy techniki ewaluacji tłumaczenia maszynowego oraz sprawdzania jego przydatności w procesie wspomagania tłumaczenia ludzkiego.

Jakość tłumaczenia maszynowego możemy oceniać na dwóch niezależnych płaszczyznach: dokładność i płynność. Płynność jest subiektywnie odbieranym odczuciem, że czytany tekst jest napisany językiem naturalnym i zrozumiałym. Systemy tłumaczenia maszynowego oparte na uczeniu głębokim z wykorzystaniem sieci neuronowych osiągają duży stopień płynności tłumaczenia. Niestety jednak ich dokładność nie zawsze jest równie wysoka.

Dokładność tłumaczenia maszynowego jest parametrem, który łatwiej zmierzyć. Wartość takich pomiarów daje obraz tego, jaka jest faktyczna jakość tłumaczenia maszynowego i jaka jest jego potencjalna przydatność we wspomaganiu tłumaczenia.

Najczęściej stosowaną techniką oceny tłumaczenia maszynowego jest ocena BLEU. Do obliczenia tej oceny potrzebny jest wynik tłumaczenia maszynowego oraz referencyjne tłumaczenie ludzkie wysokiej jakości.

### Ćwiczenie 1: Zaimplementuj program do obliczania oceny BLEU dla korpusu w folderze data. Użyj implementacji BLEU z pakietu nltk. Dodatkowe wymaganie techniczne - napisz program tak, aby nie musiał rozpakwowywać pliku zip z korpusem na dysku.

In [37]:
import os
import zipfile
import nltk.translate.bleu_score as bleu
import string

def remove_punctuation(text):
    no_punctuation_text = text.translate(str.maketrans('', '', string.punctuation))
    sentences = no_punctuation_text.split('\n')
    return [[word.lower() for word in sentence.split()] for sentence in sentences if sentence != '']

def extract_zip(input_zip):
    input_zip = zipfile.ZipFile(input_zip)
    return {name: remove_punctuation(input_zip.read(name).decode('utf-8'))
            for name in input_zip.namelist()}

def calculate_bleu(data_folder):
    if not os.path.exists(data_folder):
        output = extract_zip(data_folder + '.zip')  # keys: 'corpus_de_human.txt', 'corpus_de_nmt.txt', 'corpus_en.txt'
        human, machine = output['corpus_de_human.txt'], output['corpus_de_nmt.txt']
    else:
        with open(data_folder + '/corpus_de_human.txt', 'r') as file:
            human = [line.strip() for line in file]
        with open(data_folder + '/corpus_de_nmt.txt', 'r') as file:
            machine = [line.strip() for line in file]
    
    return bleu.corpus_bleu(human, machine)

print("BLEU Score:", calculate_bleu('data/corpus_corrected'))

BLEU Score: 3.984587822441638e-156


/Users/potoato/.pyenv/versions/3.11.0/lib/python3.11/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/Users/potoato/.pyenv/versions/3.11.0/lib/python3.11/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)


### Ćwiczenie 2: Oblicz wartość bleu na różnych fragmentach przykładowego korpusu (np. na pierwszych 100 zdaniach, zdaniach 500-600). Czy w jakimś fragmencie korpusu jakość tłumaczenia znacząco odbiega od średniej?

In [90]:
import numpy as np

def moving_window_indexes(n, window_size, step):
    return [(i, i+window_size) for i in range(0, n - window_size + 1, step)]

def analyze_bleu(data_folder):
    bleu_score = []
    output = extract_zip(data_folder + '.zip')
    human, machine = output['corpus_de_human.txt'], output['corpus_de_nmt.txt']
    idx = moving_window_indexes(len(human), 100, 100)
    for i in idx:
        bleu_score.append(bleu.corpus_bleu(human[i[0]:i[1]], machine[i[0]:i[1]]))
    avg_bleu = np.average(bleu_score)
    std_bleu = np.std(bleu_score)
    outside_bleu = [i for i, score in enumerate(bleu_score)
                    if score < avg_bleu - std_bleu]
    return bleu_score, avg_bleu, std_bleu, outside_bleu

bleu_score, avg_bleu, std_bleu, outside_bleu = analyze_bleu('data/corpus_corrected')

print("Average BLEU Score:", avg_bleu)
print("Standard Deviation of BLEU Scores:", std_bleu)
print("Values that are outside of std:", outside_bleu)

/Users/potoato/.pyenv/versions/3.11.0/lib/python3.11/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/Users/potoato/.pyenv/versions/3.11.0/lib/python3.11/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/Users/potoato/.pyenv/versions/3.11.0/lib/python3.11/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contain

Average BLEU Score: 8.234832237953338e-157
Standard Deviation of BLEU Scores: 2.470449671386047e-156
Values that are outside of std: []


Inną metodą oceny jakości tłumaczenia maszynowego jest parametr WER - Word Error Rate. Definiuje się on w następujący sposób:

$WER = \frac{S+D+I}{N}=\frac{S+D+I}{S+D+C}$

gdzie:
 * S - liczba substytucji (słów)
 * D - liczba usunięć
 * I - liczba wstawień
 * C - liczba poprawnych śłów
 * N - liczba słów w tłumaczeniu referencyjnym (N=S+D+C)

Miara ta jest zwykle używana w do oceny systemów automatycznego rozpoznawania mowy, jednak w kontekście wspomagania tłumaczenia może być rozumiana jako wielkość nakładu pracy tłumacza nad poprawieniem tłumaczenia maszynowego.

### Ćwiczenie 3: Oblicz wartość WER dla przykładowego korpusu. Skorzystaj z gotowej implementacji WER.

In [92]:
!pip install jiwer


[notice] A new release of pip available: 22.3 -> 24.0
[notice] To update, run: pip install --upgrade pip


In [128]:
from jiwer import wer


def remove_punctuation(text):
    no_punctuation_text = text.translate(str.maketrans('', '', string.punctuation))
    return no_punctuation_text

def extract_zip(input_zip):
    input_zip = zipfile.ZipFile(input_zip)
    return {name: remove_punctuation(input_zip.read(name).decode('utf-8'))
            for name in input_zip.namelist()}

def calculate_wer(data_folder):
    output = extract_zip(data_folder + '.zip')
    human, machine = output['corpus_de_human.txt'].lower(), output['corpus_de_nmt.txt'].lower()
    avg = []
    for s_h, s_m in zip(human.split('\n'), machine.split('\n')):
        if s_h == '':
            continue
        avg.append(wer(s_h, s_m))
    return wer(human, machine), np.average(avg)


In [129]:
calculate_wer('data/corpus_corrected')

(0.17324274888946956, 0.1735521656930835)

Poza wymienionymi powyżej, stosować można jeszcze inne miary oparte na porównywaniu tłumaczenia maszynowego z ludzkim. Przypomnijmy sobie jedną, którą stosowaliśmy wcześniej.

### Ćwiczenie 4: Oblicz średnią wartość dystansu Levenshteina pomiędzy zdaniami przetłumaczonymi automatycznie oraz przez człowieka. Użyj implementacji z ćwiczeń nr 2.

In [132]:
#UWAGA: poniewaz zadanie mówi o dystansie, nie bede obliczal podobienstwa levenshtein'a.

from Levenshtein import distance as levenshtein_distance

def calculate_levenshtein(data_folder):
    output = extract_zip(data_folder + '.zip')
    human, machine = output['corpus_de_human.txt'].lower(), output['corpus_de_nmt.txt'].lower()
    avg = []
    for s_h, s_m in zip(human.split('\n'), machine.split('\n')):
        if s_h == '':
            continue
        avg.append(levenshtein_distance(s_h, s_m))
    return np.average(avg)

In [133]:
calculate_levenshtein('data/corpus_corrected')

14.008

A teraz sprawdźmy coś jeszcze. W danych przykładowego korpusu znajduje się także angielski tekst źródłowy. Teoretycznie, dobre tłumaczenie niemieckie powinno zawierać jak najwięcej słów z angielskiego źródła. Wykonajmy najstępujący eksperyment:

### Ćwiczenie 5: Dla każdej trójki zdań z korpusu przykładowego wykonaj następujące kroki:
 * Przetłumacz każde angielskie słowo na niemiecki przy użyciu modułu PyDictionary.
 * Sprawdź, które z niemieckich tłumaczeń zawiera więcej spośród tych przetłumaczonych słów - automatyczne, czy ludzkie.
Następnie wypisz statystyki zbiorcze. Które tłumaczenie zawiera więcej słownikowych tłumaczeń słów ze źródła?

In [135]:
!pip install PyDictionary

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.9/147.9 kB 2.1 MB/s eta 0:00:003.4 MB/s eta 0:00:01
  Preparing metadata (setup.py) ... done
  DEPRECATION: futures is being installed using the legacy 'setup.py install' method, because it does not have a 'pyproject.toml' and the 'wheel' package is not installed. pip 23.1 will enforce this behaviour change. A possible replacement is to enable the '--use-pep517' option. Discussion can be found at https://github.com/pypa/pip/issues/8559
  Running setup.py install for futures ... done
  DEPRECATION: goslate is being installed using the legacy 'setup.py install' method, because it does not have a 'pyproject.toml' and the 'wheel' package is not installed. pip 23.1 will enforce this behaviour change. A possible replacement is to enable the '--use-pep517' option. Discussion can be found at https://github.com/pypa/pip/issues/8559
  Running setup.py install for goslate ... done

[notice] A new release of 

In [1]:
from PyDictionary import PyDictionary
import zipfile
import string
from tqdm import tqdm

def remove_punctuation(text):
    no_punctuation_text = text.translate(str.maketrans('', '', string.punctuation))
    words = no_punctuation_text.split()
    return [word.lower() for word in words if word]

def extract_zip(input_zip):
    input_zip = zipfile.ZipFile(input_zip)
    return {name: input_zip.read(name).decode('utf-8')
            for name in input_zip.namelist()}

def translate_to_german(word_list):
    dictionary = PyDictionary()
    german_translations = []
    for word in tqdm(word_list):
        try:
            translations = dictionary.translate(word, 'de')
            german_translations.extend(translations)
        except:
            pass
    return german_translations

def compare_translations(data_folder):
    output = extract_zip(data_folder + '.zip')
    human_english = remove_punctuation(output['corpus_en.txt'])
    human_german = remove_punctuation(output['corpus_de_human.txt'])
    automatic_german = translate_to_german(human_english)
    unique_human_german = set(human_german)
    unique_automatic_german = set(automatic_german)
    summary = {
        "Human Translations": len(unique_human_german),
        "Automatic Translations": len(unique_automatic_german),
        "Common Translations": len(unique_human_german.intersection(unique_automatic_german))
    }

    return summary

summary = compare_translations('data/corpus_corrected')

print("Summary Statistics:")
for key, value in summary.items():
    print(f"{key}: {value}")


  0%|          | 1/15172 [00:00<2:33:39,  1.65it/s]

Invalid Word


  0%|          | 2/15172 [00:00<1:43:31,  2.44it/s]

Invalid Word


  0%|          | 3/15172 [00:01<1:25:39,  2.95it/s]

...

Invalid Word


  8%|▊         | 1266/15172 [09:19<1:35:02,  2.44it/s]

Invalid Word


  8%|▊         | 1267/15172 [09:20<1:50:14,  2.10it/s]

Invalid Word
